In [1]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:85% !important; }</style>"))

import warnings
warnings.filterwarnings('ignore')

%reload_ext autoreload
%autoreload 2

In [4]:
import os
from pathlib import Path

import pandas as pd
import torch
import numpy as np 

import plotly.express as px

In [75]:
dataset_name = 'synthetic'
xp_name = '1107_1830'
xp_dir = Path(f'/Users/jonathanlacotte/code/numerical_results/effective_dimension_solver/{dataset_name}/single_run') / xp_name

df = pd.read_parquet(xp_dir)

dfs = []

df_dmpcg = df[df.method.isin(['dm', 'cg'])]
for sk_ in df.sketch_fn.unique():
    if sk_ == 'none':
        continue
    dfsk_ = df_dmpcg.copy()
    dfsk_['sketch_fn'] = sk_
    
    dfs.append(dfsk_)
    
dfs.append(df[df.method.isin(['pcg', 'adacg'])])

df = pd.concat(dfs, axis=0, ignore_index=True)

In [76]:
display(df.n.unique(), df.d.unique())
display(df.columns)

array([1024, 4096, 8192, 2048])

array([  32, 4096,  256,   64,  128,  512, 1024, 2048, 8192])

Index(['errors', 'gradient_norms', 'time', 'sketch_size', 'iters',
       'handshake_time', 'time_to_send_data', 'n', 'd', 'deff', 'cn',
       'pcg_sketch_size', 'ada_sketch_size', 'max_sketch_size', 'tolerance',
       'tolerance_warmup', 'n_iterations', 'n_iterations_cg', 'with_torch',
       'sketch_fn', 'num_workers', 'method', 'dtype', 'xp_id'],
      dtype='object')

# Error vs time (fixed n and d)
# Sketch size vs time (fixed n and d)

In [78]:
for cn in np.unique(df.cn):
    print(f"{cn=}")
    dfs = df[(df.n==8192)&(df.d==4096)&(df.cn==cn)]

    facet_row_name = 'deff' if dataset_name == 'synthetic' else 'reg_param'

    if facet_row_name == 'reg_param':
        dfs['reg_param'] = np.around(df['reg_param'].values, decimals=5)
    dfs = dfs.sort_values(['sketch_fn', 'method', facet_row_name, 'time'])

    fig = px.line(dfs, x='time', y='errors', facet_col='sketch_fn', facet_row=facet_row_name, color='method', line_dash='num_workers',
                  #log_x=True, 
                  log_y=True,
                 )

    fig.update_layout(height=1050)
    fig.show()

    # fig = px.line(dfs, x='iters', y='errors', facet_col='sketch_fn', facet_row=facet_row_name, color='method', line_dash='num_workers',
    #               #log_x=True, 
    #               log_y=True,
    #              )

    # fig.update_layout(height=1150)
    # fig.show()

    fig = px.line(dfs, x='time', y='sketch_size', facet_col='sketch_fn', facet_row=facet_row_name, color='method', line_dash='num_workers',
                  #log_x=True,
                  #log_y=True
                 )

    fig.update_layout(height=1050)
    fig.show()

cn=4


cn=1024


In [1556]:
df[(df.cn==1024)&(df.n==4096)&(df.d==4096)&(df.deff >= 4095)&(df.sketch_fn=='gaussian')&(df.method=='adacg')]

errors  gradient_norms      time  sketch_size  iters  \
160363  1.000000        1.000000  0.043951            0      0   
160364  0.870005        0.359335  0.057919            0      1   
160365  0.801108        0.219906  0.074602            0      2   
160366  0.758655        0.166912  0.092957            0      3   
160367  0.724959        0.118976  0.115491            0      4   
...          ...             ...       ...          ...    ...   
160443  0.368497        0.005365  2.912160         1024     77   
160444  0.367095        0.004977  2.949022         1024     78   
160445  0.365734        0.004985  2.984156         1024     79   
160446  0.364406        0.005187  3.019359         1024     80   
160447  0.363010        0.005477  3.055621         1024     81   

        handshake_time  time_to_send_data     n     d         deff  ...  \
160363        3.394026           0.043062  4096  4096  4095.694146  ...   
160364        3.394026           0.043062  4096  4096  4095.694146  ...   
160365        3.394026           0.043062  4096  4096  4095.694146  ...   
160366        3.394026           0.043062  4096  4096  4095.694146  ...   
160367        3.394026           0.043062  4096  4096  4095.694146  ...   
...                ...                ...   ...   ...          ...  ...   
160443        3.394026           0.043062  4096  4096  4095.694146  ...   
160444        3.394026           0.043062  4096  4096  4095.694146  ...   
160445        3.394026           0.043062  4096  4096  4095.694146  ...   
160446        3.394026           0.043062  4096  4096  4095.694146  ...   
160447        3.394026           0.043062  4096  4096  4095.694146  ...   

        max_sketch_size     tolerance  n_iterations  n_iterations_cg  \
160363             4096  1.000000e-10           200             1000   
160364             4096  1.000000e-10           200             1000   
160365             4096  1.000000e-10           200             1000   
160366             4096  1.000000e-10           200             1000   
160367             4096  1.000000e-10           200             1000   
...                 ...           ...           ...              ...   
160443             4096  1.000000e-10           200             1000   
160444             4096  1.000000e-10           200             1000   
160445             4096  1.000000e-10           200             1000   
160446             4096  1.000000e-10           200             1000   
160447             4096  1.000000e-10           200             1000   

        with_torch  sketch_fn  num_workers  method    dtype  xp_id  
160363        True   gaussian            1   adacg  float64   1018  
160364        True   gaussian            1   adacg  float64   1018  
160365        True   gaussian            1   adacg  float64   1018  
160366        True   gaussian            1   adacg  float64   1018  
160367        True   gaussian            1   adacg  float64   1018  
...            ...        ...          ...     ...      ...    ...  
160443        True   gaussian            1   adacg  float64   1018  
160444        True   gaussian            1   adacg  float64   1018  
160445        True   gaussian            1   adacg  float64   1018  
160446        True   gaussian            1   adacg  float64   1018  
160447        True   gaussian            1   adacg  float64   1018  

[85 rows x 23 columns]

In [1458]:
df_ = df.copy().sort_values(['n', 'd', 'deff', 'sketch_fn'])
df_['d'] = df_['d'].astype(str)
df_['deff'] = df_['deff'].astype(str)
fig = px.scatter(df_[df_.handshake_time > 0], x='d', y='handshake_time', facet_col='n', facet_row='sketch_fn', color='deff')
fig.show()

In [1100]:
df_ = df.copy().sort_values(['n', 'd', 'deff', 'sketch_fn'])
df_['d'] = df_['d'].astype(str)
df_['deff'] = df_['deff'].astype(str)
fig = px.scatter(df_[df_.time_to_send_data > 0], x='d', y='time_to_send_data', facet_col='n', facet_row='sketch_fn', color='deff')
fig.show()

# Time until sketch size > 0

In [458]:
df_mintime = (df[df.sketch_size > 0]
 .groupby(['n', 'd', 'deff', 'method', 'sketch_fn'])
 .apply(lambda x: x[x.time==np.min(x.time)])
 .drop(columns=['n', 'd', 'deff', 'method', 'sketch_fn'])
 .reset_index()
)

In [459]:
df_mintime['dstr'] = df_mintime['d'].apply(lambda x: str(x))

for n_ in np.unique(df_mintime.n):
    print(f"{n_=}")
    #df_mt_ = df_mintime[df_mintime.n==n_].groupby(['d', 'method', 'sketch_fn']).apply(lambda x: np.mean(x.time))
    
    df_mt_ = df_mintime[df_mintime.n==n_].groupby(['d', 'method', 'sketch_fn']).apply(lambda gdf: gdf.assign(z=lambda x: np.mean(x.time)))
    
    fig = px.histogram(df_mt_, 
                       x="dstr", y="time",
                       color="method", 
                       pattern_shape="sketch_fn",
                       barmode='group',
                       text_auto='.2s',
                       height=400,
                       log_y=True,
                      )
    
    fig.update_traces(textangle=0, textposition="outside", cliponaxis=False)
    fig.show()

n_=1024


n_=2048


n_=4096


# Sketch times experiments

In [320]:
xp_name = '0110_1118'
xp_dir = Path(f'/Users/jonathanlacotte/code/numerical_results/effective_dimension_solver/sketch_times') / xp_name

df = pd.read_parquet(xp_dir)

df_ = df.set_index(['n', 'd', 'sketch_size', 'sketch_fn'])

dfs = []
for c_ in df_:
    df_tmp_ = df_[[c_]].rename(columns={c_: 'time'})
    df_tmp_['method'] = c_
    dfs.append(df_tmp_.reset_index())
    
df = pd.concat(dfs, axis=0, ignore_index=True).sort_values(['n', 'd', 'sketch_size', 'method', 'sketch_fn'])


In [321]:
for n_ in np.unique(df.n):
    
    dfn_ = df[df.n==n_]
    dfn_['d-m'] = dfn_[['d', 'sketch_size']].apply(lambda x: '_'.join([str(x[0]), str(x[1])]), axis=1)
        
    print(f"{n_=}")
    
    dfn_['d'] = dfn_['d'].apply(lambda x: str(x))
    dfn_['sketch_size'] = dfn_['sketch_size'].apply(lambda x: str(x))
    
    #dfnm_ = dfn_[dfn_.sketch_size==sketch_size]
    fig = px.histogram(dfn_, 
                       x="sketch_size", 
                       y="time",
                       color="method", 
                       pattern_shape="sketch_fn",
                       barmode='group',
                       text_auto='.2s',
                       height=900,
                       facet_row='d'
                       #orientation='h'
                      )

    fig.update_traces(textangle=0, textposition="outside", cliponaxis=False)
    fig.show()

n_=1024


n_=2048


n_=4096


In [240]:
a = torch.randn(10,2)
b = a.view(-1,1)

In [241]:
print(f"{hex(a.storage().data_ptr())}, {hex(b.storage().data_ptr())}")

0x7fc65ffffd00, 0x7fc65ffffd00


In [210]:
a.data_ptr()

140489986667648

In [211]:
b.data_ptr()

140490058336064

In [273]:
id(a[0,0].item())

140489292216880

In [226]:
id(a.data)

for _ in range(5):
    print(f"{hex(a.storage().data_ptr())}, {hex(id(a.storage()))}")

0x7fc65fbff480, 0x7fc65d271dc0
0x7fc65fbff480, 0x7fc65d271eb0
0x7fc65fbff480, 0x7fc65d271520
0x7fc65fbff480, 0x7fc65d271a30
0x7fc65fbff480, 0x7fc65d271f10


In [227]:
a.storage()

 0.6987689733505249
 -0.8243185877799988
 -1.5541555881500244
 1.8257452249526978
 -0.8122731447219849
 0.2177259922027588
 0.37033891677856445
 -1.464563250541687
 -0.03020557016134262
 0.9156861901283264
[torch.storage.TypedStorage(dtype=torch.float32, device=cpu) of size 10]

In [233]:
a = np.random.randn(10, 2)
print(f"{a.base=}")

b = a.reshape((-1,1))
print(f"{a.base=}")
print(f"{b.base=}")

a.base=None
a.base=None
b.base=array([[-0.79299597, -2.51794325],
       [-1.3811076 ,  0.86479036],
       [ 0.99046681, -0.17356514],
       [-0.9947673 ,  0.3683329 ],
       [-0.07896991, -1.60049473],
       [-0.43773279, -0.74872686],
       [-0.24561208, -0.18622148],
       [ 0.31965429,  0.28730981],
       [ 1.08995711, -0.09796448],
       [-0.5589049 , -0.16891777]])


In [229]:
for _ in range(5):
    print(id(a))

140489283698832
140489283698832
140489283698832
140489283698832
140489283698832


In [274]:
class SomeClass:
    
    def __init__(self, a):
        self.a = a
        
a = torch.randn(10, 2)
cl_ = SomeClass(a)

In [275]:
print(hex(a.data_ptr()), hex(cl_.a.data_ptr()))

0x7fc66374d6c0 0x7fc66374d6c0


In [278]:
a.data.untyped_storage().data_ptr()

140490048853696

In [279]:
torch.multiprocessing.cpu_count()

12

In [280]:
import os 
os.cpu_count()

12

In [283]:
torch.get_num_thread()

AttributeError: module 'torch' has no attribute 'get_num_thread'

In [291]:
torch.seed()

15287086628140756066

# Numerical stability stuffs

In [730]:
def compute_nu(sigma, de, max_nu=8):
    def compute_de(nu):
        return (sigma ** 2 / (sigma ** 2 + nu ** 2)).sum() / (sigma[0] ** 2 / (sigma[0] ** 2 + nu ** 2))

    nu = 1.
    de_ = compute_de(nu)
    while de_ >= de and nu <= max_nu:
        nu = 2 * nu
        de_ = compute_de(nu)
    # binary search
    nu_max = nu
    nu_min = 0.
    nu = (nu_max + nu_min) / 2
    de_ = compute_de(nu)
    iteration = 0
    while np.abs(de_ - de) > 1 and iteration <= 10000:
        if de_ > de:
            nu_min = nu
            nu = (nu_min + nu_max) / 2
            de_ = compute_de(nu)
        else:
            nu_max = nu
            nu = (nu_min + nu_max) / 2
            de_ = compute_de(nu)
        iteration += 1
    return max(1e-10, nu), de_

def cholesky(h, lower=False):
    if lower:
        return torch.linalg.cholesky(h)
    else:
        return torch.linalg.cholesky(h).mH
    
    
def get_max_sval_approx(a, m=6, niter=2):
    
    m = 6 if m is None else m
    n, d = a.shape[-2:]
    
    if m > n or m > d:
        sigma = torch.linalg.svdvals(a)
        return sigma[0].item()
    
    a_t = a.T
    dtype = a.dtype
    device = a.device
    
    s = torch.randn(n, m, dtype=dtype, device=device)
    q = torch.linalg.qr(a_t @ s).Q
    for i in range(niter):
        q = torch.linalg.qr(a @ q).Q
        q = torch.linalg.qr(a_t @ q).Q

    b_t = a @ q
    sigma = torch.linalg.svdvals(b_t)

    return sigma[0].item()

In [728]:
def make_synthetic_example(n, d, deff, with_torch, eig_val=0.95, dtype=torch.float32):
    if with_torch:
        a = 1. / np.sqrt(n) * torch.randn(d, d, dtype=dtype) / np.sqrt(d)
        b = 1. / np.sqrt(n) * torch.randn(n, 1, dtype=dtype)
        _, sigma, vh = torch.linalg.svd(a, full_matrices=False)
        sigma = torch.tensor([max(eig_val ** jj, 1e-3) for jj in range(a.shape[1])], dtype=dtype).reshape((-1, 1))
        u = torch.randn(n, d, dtype=dtype) / np.sqrt(n)
        a = u @ (sigma * vh)
        sigma = torch.linalg.svdvals(a)
        reg_param, deff_ = compute_nu(sigma, deff)
        deff_ = deff_.item()
        print(f"{a.dtype=}")
    else:
        a = 1. / np.sqrt(n) * np.random.randn(d, d) / np.sqrt(d)
        b = np.array(1. / np.sqrt(n) * np.random.randn(n, 1), dtype=np.float32)
        _, sigma, vh = np.linalg.svd(a, full_matrices=False)
        sigma = np.array([max(eig_val ** jj, 1e-3) for jj in range(a.shape[1])]).reshape((-1, 1))
        u = np.random.randn(n, d) / np.sqrt(n)
        a = np.array(u @ (sigma * vh), dtype=np.float32)
        sigma = np.linalg.svd(a, compute_uv=False)
        reg_param, deff_ = compute_nu(sigma, deff)

    return a, b, reg_param, deff_

# Condition number and deff 

In [1152]:
n = 4096
d = 1024
cond_number = 1000
deff = 128

In [1153]:
a, b, reg_param, deff_ = make_synthetic_example(n, d, deff, cond_number, with_torch=True)

eig_val=0.9932768474363539


In [1283]:
d = 1024
dtype=torch.float32

for deff_target in [32, 64, 128, 256, 512, 1024]:
    for cn_target in [1.5, 2, 5, 10, 32, 64, 128, 256, 1024, 2048]:
        exponent, eig_val, deff, cn, sigma, reg_param = find_exponent_eig_val(d=d, deff_target=deff_target, cn_target=cn_target, dtype=dtype)
        print(f"\n{exponent=}, {eig_val=}, {deff_target=}, {deff=}, {cn_target=}, {cn=}, {reg_param=}")


exponent=1, eig_val=0.98, deff_target=32, deff=31.872940063476562, cn_target=1.5, cn=1.2805083990097046, reg_param=1.2502913190169074

exponent=1, eig_val=0.97, deff_target=32, deff=31.2979679107666, cn_target=2, cn=2.0388453006744385, reg_param=0.5628209903982591

exponent=1, eig_val=0.95, deff_target=32, deff=32.0004768371582, cn_target=5, cn=4.672679424285889, reg_param=0.2190858260889348

exponent=7, eig_val=0.99, deff_target=32, deff=32.376441955566406, cn_target=10, cn=9.169168472290039, reg_param=0.10971554653596802

exponent=11, eig_val=0.99, deff_target=32, deff=31.79499626159668, cn_target=32, cn=31.667295455932617, reg_param=0.031593918283848894

exponent=13, eig_val=0.99, deff_target=32, deff=32.21051025390625, cn_target=64, cn=62.625755310058594, reg_param=0.01596959263342507

exponent=3, eig_val=0.95, deff_target=32, deff=31.897119522094727, cn_target=128, cn=122.58250427246094, reg_param=0.008157429808213157

exponent=6, eig_val=0.97, deff_target=32, deff=32.71120834350

In [1284]:
def make_synthetic_example(n, d, deff, cn, dtype=torch.float32):
    a = 1. / np.sqrt(n) * torch.randn(d, d, dtype=dtype) / np.sqrt(d)
    b = 1. / np.sqrt(n) * torch.randn(n, 1, dtype=dtype)
    _, _, vh = torch.linalg.svd(a, full_matrices=False)
    
    exponent, eig_val, deff_, cn_, sigma, reg_param = find_exponent_eig_val(d=d, deff_target=deff, cn_target=cn, dtype=dtype)
    sigma = sigma.reshape((-1,1))
    
    u = torch.randn(n, d, dtype=dtype) / np.sqrt(n)
    a = u @ (sigma * vh)

    return a, b, reg_param, deff_, cn_

In [1285]:
a, b, reg_param, deff_, cn_ = make_synthetic_example(2048, 1024, 512, 500)

In [1286]:
deff_

511.9687805175781

In [1287]:
cn_

465.5384216308594

In [1288]:
reg_param

0.002145726384124302